In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0302_MR1_mpr-3_154.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0114_MR1_mpr-1_130.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0150_MR1_mpr-3_129.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0253_MR1_mpr-3_113.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0349_MR1_mpr-4_150.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0045_MR1_mpr-2_102.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0209_MR1_mpr-4_128.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0074_MR1_mpr-4_140.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0330_MR1_mpr-4_112.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0234_MR1_mpr-4_113.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0065_MR1_mpr-3_131.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0207_MR1_mpr-2_106.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0375_MR1_mpr-1_136.jpg
/kaggle/input/imagesoasis/Data/Non Demented/OAS1_0160_MR1_mpr-4_

In [2]:
import tensorflow as tf
from tensorflow.keras import datasets, layers, models#type:ignore
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from tensorflow.keras.preprocessing import image #type:ignore
from tensorflow.keras.callbacks import EarlyStopping#type:ignore
from tensorflow.keras.preprocessing.image import ImageDataGenerator#type:ignore
from sklearn.metrics import confusion_matrix, classification_report
import seaborn as sns
from sklearn.metrics import matthews_corrcoef
from sklearn.metrics import precision_recall_curve, average_precision_score,precision_score, recall_score, f1_score
from sklearn.metrics import roc_curve, auc

In [3]:
print("Num GPUs Available: ", len(tf.config.experimental.list_physical_devices('GPU')))

# Set memory growth to prevent TensorFlow from consuming all GPU memory at once
gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
    try:
        for gpu in gpus:
            tf.config.experimental.set_memory_growth(gpu, True)
    except RuntimeError as e:
        print(e)

Num GPUs Available:  1


In [4]:
# train_datagen = ImageDataGenerator(rescale=1./255,
#                                    validation_split = 0.2)
train_datagen = ImageDataGenerator(rescale=1./255,
                                  rotation_range=20,
                                  width_shift_range=0.2,
                                  height_shift_range=0.2,
                                  shear_range=0.2,
                                  zoom_range=0.2,
                                  horizontal_flip=True,
                                  fill_mode='nearest')
train_generator = train_datagen.flow_from_directory(
    '/kaggle/input/imagesoasis/Data',
    target_size=(250, 250),
    batch_size=16,
    class_mode='categorical'
)

test_datagen = ImageDataGenerator(
    rescale=1./255,
    validation_split = 0.2
)

test_generator = test_datagen.flow_from_directory(
    '/kaggle/input/imagesoasis/Data',
    target_size=(250, 250),
    batch_size=16,
    class_mode='categorical',
    shuffle=False  # Important for confusion matrix
)


Found 86437 images belonging to 4 classes.
Found 86437 images belonging to 4 classes.


In [5]:
model = models.Sequential([
    layers.Conv2D(32, (3, 3), activation='relu', input_shape=(250, 250, 3)),
    layers.BatchNormalization(),
    layers.MaxPooling2D((2, 2)),

    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.BatchNormalization(),
    layers.MaxPooling2D((2, 2)),

    layers.Conv2D(128, (3, 3), activation='relu'),
    layers.BatchNormalization(),
    layers.MaxPooling2D((2, 2)),

    layers.Conv2D(256, (3, 3), activation='relu'),
    layers.BatchNormalization(),
    layers.MaxPooling2D((2, 2)),

    layers.Conv2D(512, (3, 3), activation='relu'),
    layers.BatchNormalization(),
    layers.MaxPooling2D((2, 2)),

    layers.Conv2D(1024, (3, 3), activation='relu'),
    layers.BatchNormalization(),
    layers.MaxPooling2D((2, 2)),
    
    layers.Flatten(),
    
    # Add more dense layers
    layers.Dense(1024, activation='relu'),
    layers.BatchNormalization(),
    layers.Dropout(0.4),

    layers.Dense(512, activation='relu'),
    layers.BatchNormalization(),
    

    layers.Dense(256, activation='relu'),
    layers.BatchNormalization(),
    layers.Dropout(0.4),

    # Final output layer
    layers.Dense(4, activation='softmax')
])


/usr/local/lib/python3.10/dist-packages/keras/src/layers/convolutional/base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [6]:
model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=1e-4),
              loss=tf.keras.losses.CategoricalCrossentropy(),
              metrics=['accuracy'])
early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)


In [7]:
history = model.fit(
    train_generator,
    epochs=20,
    validation_data=test_generator,
    callbacks=[early_stopping],
    batch_size=64
)

Epoch 1/20


/usr/local/lib/python3.10/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:122: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


5403/5403 ━━━━━━━━━━━━━━━━━━━━ 1653s 303ms/step - accuracy: 0.5576 - loss: 1.1986 - val_accuracy: 0.7871 - val_loss: 0.4906
Epoch 2/20
5403/5403 ━━━━━━━━━━━━━━━━━━━━ 1364s 252ms/step - accuracy: 0.7667 - loss: 0.5650 - val_accuracy: 0.7906 - val_loss: 0.5108
Epoch 3/20
5403/5403 ━━━━━━━━━━━━━━━━━━━━ 1381s 255ms/step - accuracy: 0.7815 - loss: 0.5113 - val_accuracy: 0.8078 - val_loss: 0.4366
Epoch 4/20
5403/5403 ━━━━━━━━━━━━━━━━━━━━ 1399s 259ms/step - accuracy: 0.7968 - loss: 0.4735 - val_accuracy: 0.8373 - val_loss: 0.3747
Epoch 5/20
5403/5403 ━━━━━━━━━━━━━━━━━━━━ 1423s 263ms/step - accuracy: 0.8118 - loss: 0.4408 - val_accuracy: 0.8264 - val_loss: 0.4340
Epoch 6/20
5403/5403 ━━━━━━━━━━━━━━━━━━━━ 1425s 263ms/step - accuracy: 0.8288 - loss: 0.4054 - val_accuracy: 0.8772 - val_loss: 0.3064
Epoch 7/20
5403/5403 ━━━━━━━━━━━━━━━━━━━━ 1449s 268ms/step - accuracy: 0.8438 - loss: 0.3720 - val_accuracy: 0.9061 - val_loss: 0.2297
Epoch 8/20
5403/5403 ━━━━━━━━━━━━━━━━━━━━ 1350s 250ms/step - accur